Detección de barras en galaxias - Modelos Alternativos

Proyecto integrador MNA

Integrantes

Jonathan Jesús Marmolejo Hernández - A01795195

Isaid Posadas Oropeza - A01795015

Luis Daniel Ortega Muñoz - A01795197


# Modelo de ensamble heterogéneo Voting con YOLOv8s, YOLOv8m, YOLOv8l y YOLOv8x
      

In [1]:
from google.colab import drive
drive.mount('/content/drive')

Mounted at /content/drive


##Instalar YOLOv8

In [2]:
!pip install ultralytics > /dev/null 2>&1

In [3]:
from ultralytics import YOLO

# Verificar versión
import ultralytics
print(f"Ultralytics versión: {ultralytics.__version__}")


Creating new Ultralytics Settings v0.0.6 file ✅ 
View Ultralytics Settings with 'yolo settings' or at '/root/.config/Ultralytics/settings.json'
Update Settings with 'yolo settings key=value', i.e. 'yolo settings runs_dir=path/to/dir'. For help see https://docs.ultralytics.com/quickstart/#ultralytics-settings.
Ultralytics versión: 8.3.146


In [4]:
from ultralytics import settings
settings.reset()  # Reinicia configuraciones de cache si hay conflictos

# Ensamble Voting

### Voting con umbral de confianza de 0.25, IoU de 0.5 y número de votos mínimo de 3 de los 4 modelos

In [7]:
from google.colab import drive
drive.mount('/content/drive')

from ultralytics import YOLO
import os
import cv2
import numpy as np
from tqdm import tqdm
import shutil
import pandas as pd

# === Umbral de confianza mínimo ===
CONFIDENCE_THRESHOLD = 0.25

# === Rutas ===
model_paths = [
    '/content/drive/MyDrive/MNA_ProyectoIntegrador/modelos_yolo/best_v8s_LogDiff.pt',
    '/content/drive/MyDrive/MNA_ProyectoIntegrador/modelos_yolo/best_v8m_LogDiff.pt',
    '/content/drive/MyDrive/MNA_ProyectoIntegrador/modelos_yolo/best_v8l_LogDiff.pt',
    '/content/drive/MyDrive/MNA_ProyectoIntegrador/modelos_yolo/best_v8x_LogDiff.pt'
]

image_dir = '/content/drive/MyDrive/MNA_ProyectoIntegrador/galaxy_dataset_2/images/val'
output_dir = '/content/drive/MyDrive/MNA_ProyectoIntegrador/voting_ensemble_results'
csv_output_path = os.path.join(output_dir, 'predicciones_ensemble.csv')

# === Limpiar carpeta de salida ===
if os.path.exists(output_dir):
    shutil.rmtree(output_dir)
os.makedirs(output_dir)

# === Cargar modelos ===
models = [YOLO(p) for p in model_paths]

# === Funciones auxiliares ===
def iou(box1, box2):
    xA, yA = max(box1[0], box2[0]), max(box1[1], box2[1])
    xB, yB = min(box1[2], box2[2]), min(box1[3], box2[3])
    interArea = max(0, xB - xA) * max(0, yB - yA)
    box1Area = (box1[2] - box1[0]) * (box1[3] - box1[1])
    box2Area = (box2[2] - box2[0]) * (box2[3] - box2[1])
    return interArea / float(box1Area + box2Area - interArea + 1e-6)

def ensemble_predictions(results_list, iou_thr=0.5, vote_threshold=3):
    all_boxes = []
    for model_idx, result in enumerate(results_list):
        for box in result.boxes:
            conf = box.conf[0].cpu().item()
            if conf < CONFIDENCE_THRESHOLD:
                continue  # Filtrar detecciones de baja confianza

            coords = box.xyxy[0].cpu().numpy()
            cls = int(box.cls[0].cpu().item())
            all_boxes.append((coords, conf, cls, model_idx))  # incluir ID del modelo

    grouped = []
    used = set()

    for i in range(len(all_boxes)):
        if i in used:
            continue
        group = [all_boxes[i]]
        model_ids = {all_boxes[i][3]}

        for j in range(i + 1, len(all_boxes)):
            if j in used:
                continue
            if all_boxes[i][2] == all_boxes[j][2] and iou(all_boxes[i][0], all_boxes[j][0]) >= iou_thr:
                if all_boxes[j][3] not in model_ids:
                    group.append(all_boxes[j])
                    model_ids.add(all_boxes[j][3])
                    used.add(j)
        used.add(i)

        if len(model_ids) >= vote_threshold:
            boxes_np = np.array([g[0] for g in group])
            avg_box = boxes_np.mean(axis=0)
            avg_conf = np.mean([g[1] for g in group])
            cls = group[0][2]
            grouped.append((avg_box, avg_conf, cls, len(model_ids)))

    # Validar conflictos
    final_detections = []
    for i, (box_i, conf_i, cls_i, votes_i) in enumerate(grouped):
        conflict = False
        for j, (box_j, conf_j, cls_j, votes_j) in enumerate(grouped):
            if i == j:
                continue
            if iou(box_i, box_j) >= iou_thr and cls_i != cls_j:
                if votes_i > votes_j or (votes_i == votes_j and conf_i > conf_j):
                    continue
                else:
                    conflict = True
                    break
        if not conflict:
            final_detections.append((box_i, conf_i, cls_i, votes_i))

    return final_detections

def convert_to_yolo_format(box, img_width, img_height):
    x1, y1, x2, y2 = box
    x_center = (x1 + x2) / 2.0 / img_width
    y_center = (y1 + y2) / 2.0 / img_height
    width = (x2 - x1) / img_width
    height = (y2 - y1) / img_height
    return x_center, y_center, width, height

# === Procesamiento ===
image_paths = [os.path.join(image_dir, f) for f in os.listdir(image_dir) if f.lower().endswith(('.jpg', '.png'))]
csv_data = []

for img_path in tqdm(image_paths):
    img = cv2.imread(img_path)
    img_height, img_width = img.shape[:2]
    results_list = [model(img)[0] for model in models]
    final_detections = ensemble_predictions(results_list)

    filename = os.path.splitext(os.path.basename(img_path))[0]
    cv2.imwrite(os.path.join(output_dir, f"{filename}.jpg"), img)

    with open(os.path.join(output_dir, f"{filename}.txt"), 'w') as f:
        for box, conf, cls, votes in final_detections:
            x_center, y_center, width, height = convert_to_yolo_format(box, img_width, img_height)
            f.write(f"{cls} {x_center:.6f} {y_center:.6f} {width:.6f} {height:.6f} {conf:.4f}\n")
            csv_data.append({
                "image": f"{filename}.jpg",
                "class": cls,
                "x_center": x_center,
                "y_center": y_center,
                "width": width,
                "height": height,
                "confidence": conf,
                "votes": votes
            })

# Guardar CSV
pd.DataFrame(csv_data).to_csv(csv_output_path, index=False)

print(f"\n Proceso completo. Revisa la carpeta:\n{output_dir}")
print(f" CSV resumen creado en:\n{csv_output_path}")


Drive already mounted at /content/drive; to attempt to forcibly remount, call drive.mount("/content/drive", force_remount=True).


  0%|          | 0/1338 [00:00<?, ?it/s]


0: 640x640 1 barra, 16.3ms
Speed: 2.0ms preprocess, 16.3ms inference, 1.6ms postprocess per image at shape (1, 3, 640, 640)

0: 640x640 1 barra, 36.9ms
Speed: 1.9ms preprocess, 36.9ms inference, 1.6ms postprocess per image at shape (1, 3, 640, 640)

0: 640x640 1 barra, 59.1ms
Speed: 2.4ms preprocess, 59.1ms inference, 1.6ms postprocess per image at shape (1, 3, 640, 640)

0: 640x640 1 barra, 64.5ms
Speed: 1.9ms preprocess, 64.5ms inference, 1.4ms postprocess per image at shape (1, 3, 640, 640)


  0%|          | 1/1338 [00:02<1:00:06,  2.70s/it]


0: 640x640 1 barra, 8.9ms
Speed: 1.9ms preprocess, 8.9ms inference, 1.4ms postprocess per image at shape (1, 3, 640, 640)

0: 640x640 1 barra, 18.7ms
Speed: 2.3ms preprocess, 18.7ms inference, 1.6ms postprocess per image at shape (1, 3, 640, 640)

0: 640x640 1 barra, 37.0ms
Speed: 2.1ms preprocess, 37.0ms inference, 1.5ms postprocess per image at shape (1, 3, 640, 640)

0: 640x640 2 barras, 63.1ms
Speed: 1.9ms preprocess, 63.1ms inference, 1.5ms postprocess per image at shape (1, 3, 640, 640)


...


0: 640x640 (no detections), 9.3ms
Speed: 2.0ms preprocess, 9.3ms inference, 0.7ms postprocess per image at shape (1, 3, 640, 640)

0: 640x640 1 barra, 19.0ms
Speed: 1.8ms preprocess, 19.0ms inference, 1.5ms postprocess per image at shape (1, 3, 640, 640)

0: 640x640 1 barra, 33.0ms
Speed: 2.0ms preprocess, 33.0ms inference, 1.4ms postprocess per image at shape (1, 3, 640, 640)

0: 640x640 2 barras, 62.0ms
Speed: 2.3ms preprocess, 62.0ms inference, 2.1ms postprocess per image at shape (1, 3, 640, 640)


100%|█████████▉| 1337/1338 [04:08<00:00,  5.63it/s]


0: 640x640 2 barras, 10.9ms
Speed: 2.7ms preprocess, 10.9ms inference, 1.5ms postprocess per image at shape (1, 3, 640, 640)

0: 640x640 (no detections), 17.4ms
Speed: 1.9ms preprocess, 17.4ms inference, 0.7ms postprocess per image at shape (1, 3, 640, 640)

0: 640x640 (no detections), 35.0ms
Speed: 2.1ms preprocess, 35.0ms inference, 1.2ms postprocess per image at shape (1, 3, 640, 640)

0: 640x640 (no detections), 62.8ms
Speed: 2.7ms preprocess, 62.8ms inference, 0.9ms postprocess per image at shape (1, 3, 640, 640)


100%|██████████| 1338/1338 [04:08<00:00,  5.38it/s]


✅ Proceso completo. Revisa la carpeta:
/content/drive/MyDrive/MNA_ProyectoIntegrador/voting_ensemble_results
📄 CSV resumen creado en:
/content/drive/MyDrive/MNA_ProyectoIntegrador/voting_ensemble_results/predicciones_ensemble.csv


In [8]:
from sklearn.metrics import precision_score, recall_score, f1_score
import os

# Rutas
gt_dir = '/content/drive/MyDrive/MNA_ProyectoIntegrador/galaxy_dataset_2/labels/val'
pred_dir = '/content/drive/MyDrive/MNA_ProyectoIntegrador/voting_ensemble_results'

y_true = []
y_pred = []

# Archivos en el conjunto de validación
gt_files = [f for f in os.listdir(gt_dir) if f.endswith('.txt')]

for fname in gt_files:
    gt_path = os.path.join(gt_dir, fname)
    pred_path = os.path.join(pred_dir, fname)

    # === Ground truth ===
    with open(gt_path, 'r') as f:
        gt_lines = f.readlines()
    has_bar_gt = len(gt_lines) > 0
    y_true.append(1 if has_bar_gt else 0)

    # === Predicción del ensamble ===
    if os.path.exists(pred_path):
        with open(pred_path, 'r') as f:
            pred_lines = f.readlines()
        has_bar_pred = len(pred_lines) > 0
    else:
        has_bar_pred = False

    y_pred.append(1 if has_bar_pred else 0)

# === Métricas
precision = precision_score(y_true, y_pred)
recall = recall_score(y_true, y_pred)
f1 = f1_score(y_true, y_pred)

# === Resultados
print(" Evaluación del ensamble Voting:")
print(f"Precision: {precision:.4f}")
print(f"Recall:    {recall:.4f}")
print(f"F1-score:  {f1:.4f}")


 Evaluación del ensamble Voting:
Precision: 0.6088
Recall:    0.9118
F1-score:  0.7301


### Voting con umbral de confianza de 0.4, IoU de 0.5 y número de votos mínimo de 3 de los 4 modelos

In [9]:
from google.colab import drive
drive.mount('/content/drive')

from ultralytics import YOLO
import os
import cv2
import numpy as np
from tqdm import tqdm
import shutil
import pandas as pd

# === Umbral de confianza mínimo ===
CONFIDENCE_THRESHOLD = 0.4

# === Rutas ===
model_paths = [
    '/content/drive/MyDrive/MNA_ProyectoIntegrador/modelos_yolo/best_v8s_LogDiff.pt',
    '/content/drive/MyDrive/MNA_ProyectoIntegrador/modelos_yolo/best_v8m_LogDiff.pt',
    '/content/drive/MyDrive/MNA_ProyectoIntegrador/modelos_yolo/best_v8l_LogDiff.pt',
    '/content/drive/MyDrive/MNA_ProyectoIntegrador/modelos_yolo/best_v8x_LogDiff.pt'
]

image_dir = '/content/drive/MyDrive/MNA_ProyectoIntegrador/galaxy_dataset_2/images/val'
output_dir = '/content/drive/MyDrive/MNA_ProyectoIntegrador/voting_ensemble_results'
csv_output_path = os.path.join(output_dir, 'predicciones_ensemble.csv')

# === Limpiar carpeta de salida ===
if os.path.exists(output_dir):
    shutil.rmtree(output_dir)
os.makedirs(output_dir)

# === Cargar modelos ===
models = [YOLO(p) for p in model_paths]

# === Funciones auxiliares ===
def iou(box1, box2):
    xA, yA = max(box1[0], box2[0]), max(box1[1], box2[1])
    xB, yB = min(box1[2], box2[2]), min(box1[3], box2[3])
    interArea = max(0, xB - xA) * max(0, yB - yA)
    box1Area = (box1[2] - box1[0]) * (box1[3] - box1[1])
    box2Area = (box2[2] - box2[0]) * (box2[3] - box2[1])
    return interArea / float(box1Area + box2Area - interArea + 1e-6)

def ensemble_predictions(results_list, iou_thr=0.5, vote_threshold=3):
    all_boxes = []
    for model_idx, result in enumerate(results_list):
        for box in result.boxes:
            conf = box.conf[0].cpu().item()
            if conf < CONFIDENCE_THRESHOLD:
                continue  # Filtrar detecciones de baja confianza

            coords = box.xyxy[0].cpu().numpy()
            cls = int(box.cls[0].cpu().item())
            all_boxes.append((coords, conf, cls, model_idx))  # incluir ID del modelo

    grouped = []
    used = set()

    for i in range(len(all_boxes)):
        if i in used:
            continue
        group = [all_boxes[i]]
        model_ids = {all_boxes[i][3]}

        for j in range(i + 1, len(all_boxes)):
            if j in used:
                continue
            if all_boxes[i][2] == all_boxes[j][2] and iou(all_boxes[i][0], all_boxes[j][0]) >= iou_thr:
                if all_boxes[j][3] not in model_ids:
                    group.append(all_boxes[j])
                    model_ids.add(all_boxes[j][3])
                    used.add(j)
        used.add(i)

        if len(model_ids) >= vote_threshold:
            boxes_np = np.array([g[0] for g in group])
            avg_box = boxes_np.mean(axis=0)
            avg_conf = np.mean([g[1] for g in group])
            cls = group[0][2]
            grouped.append((avg_box, avg_conf, cls, len(model_ids)))

    # Validar conflictos
    final_detections = []
    for i, (box_i, conf_i, cls_i, votes_i) in enumerate(grouped):
        conflict = False
        for j, (box_j, conf_j, cls_j, votes_j) in enumerate(grouped):
            if i == j:
                continue
            if iou(box_i, box_j) >= iou_thr and cls_i != cls_j:
                if votes_i > votes_j or (votes_i == votes_j and conf_i > conf_j):
                    continue
                else:
                    conflict = True
                    break
        if not conflict:
            final_detections.append((box_i, conf_i, cls_i, votes_i))

    return final_detections

def convert_to_yolo_format(box, img_width, img_height):
    x1, y1, x2, y2 = box
    x_center = (x1 + x2) / 2.0 / img_width
    y_center = (y1 + y2) / 2.0 / img_height
    width = (x2 - x1) / img_width
    height = (y2 - y1) / img_height
    return x_center, y_center, width, height

# === Procesamiento ===
image_paths = [os.path.join(image_dir, f) for f in os.listdir(image_dir) if f.lower().endswith(('.jpg', '.png'))]
csv_data = []

for img_path in tqdm(image_paths):
    img = cv2.imread(img_path)
    img_height, img_width = img.shape[:2]
    results_list = [model(img)[0] for model in models]
    final_detections = ensemble_predictions(results_list)

    filename = os.path.splitext(os.path.basename(img_path))[0]
    cv2.imwrite(os.path.join(output_dir, f"{filename}.jpg"), img)

    with open(os.path.join(output_dir, f"{filename}.txt"), 'w') as f:
        for box, conf, cls, votes in final_detections:
            x_center, y_center, width, height = convert_to_yolo_format(box, img_width, img_height)
            f.write(f"{cls} {x_center:.6f} {y_center:.6f} {width:.6f} {height:.6f} {conf:.4f}\n")
            csv_data.append({
                "image": f"{filename}.jpg",
                "class": cls,
                "x_center": x_center,
                "y_center": y_center,
                "width": width,
                "height": height,
                "confidence": conf,
                "votes": votes
            })

# Guardar CSV
pd.DataFrame(csv_data).to_csv(csv_output_path, index=False)

print(f"\n Proceso completo. Revisa la carpeta:\n{output_dir}")
print(f" CSV resumen creado en:\n{csv_output_path}")


Drive already mounted at /content/drive; to attempt to forcibly remount, call drive.mount("/content/drive", force_remount=True).


  0%|          | 0/1338 [00:00<?, ?it/s]


0: 640x640 1 barra, 16.3ms
Speed: 2.2ms preprocess, 16.3ms inference, 1.8ms postprocess per image at shape (1, 3, 640, 640)

0: 640x640 1 barra, 37.0ms
Speed: 2.1ms preprocess, 37.0ms inference, 1.7ms postprocess per image at shape (1, 3, 640, 640)

0: 640x640 1 barra, 60.0ms
Speed: 2.1ms preprocess, 60.0ms inference, 2.2ms postprocess per image at shape (1, 3, 640, 640)

0: 640x640 1 barra, 65.3ms
Speed: 1.9ms preprocess, 65.3ms inference, 1.5ms postprocess per image at shape (1, 3, 640, 640)


  0%|          | 1/1338 [00:02<1:01:53,  2.78s/it]


0: 640x640 1 barra, 10.0ms
Speed: 2.0ms preprocess, 10.0ms inference, 1.6ms postprocess per image at shape (1, 3, 640, 640)

0: 640x640 1 barra, 18.8ms
Speed: 2.0ms preprocess, 18.8ms inference, 1.4ms postprocess per image at shape (1, 3, 640, 640)

0: 640x640 1 barra, 37.4ms
Speed: 1.9ms preprocess, 37.4ms inference, 1.6ms postprocess per image at shape (1, 3, 640, 640)

0: 640x640 2 barras, 64.3ms
Speed: 1.9ms preprocess, 64.3ms inference, 1.6ms postprocess per image at shape (1, 3, 640, 640)


...


0: 640x640 (no detections), 10.1ms
Speed: 2.7ms preprocess, 10.1ms inference, 0.8ms postprocess per image at shape (1, 3, 640, 640)

0: 640x640 1 barra, 18.0ms
Speed: 2.3ms preprocess, 18.0ms inference, 1.6ms postprocess per image at shape (1, 3, 640, 640)

0: 640x640 1 barra, 36.8ms
Speed: 1.8ms preprocess, 36.8ms inference, 2.0ms postprocess per image at shape (1, 3, 640, 640)

0: 640x640 2 barras, 62.0ms
Speed: 2.1ms preprocess, 62.0ms inference, 2.5ms postprocess per image at shape (1, 3, 640, 640)


100%|█████████▉| 1337/1338 [04:10<00:00,  5.40it/s]


0: 640x640 2 barras, 10.4ms
Speed: 2.7ms preprocess, 10.4ms inference, 2.0ms postprocess per image at shape (1, 3, 640, 640)

0: 640x640 (no detections), 18.0ms
Speed: 1.8ms preprocess, 18.0ms inference, 0.7ms postprocess per image at shape (1, 3, 640, 640)

0: 640x640 (no detections), 36.5ms
Speed: 2.0ms preprocess, 36.5ms inference, 1.0ms postprocess per image at shape (1, 3, 640, 640)

0: 640x640 (no detections), 64.0ms
Speed: 2.1ms preprocess, 64.0ms inference, 1.0ms postprocess per image at shape (1, 3, 640, 640)


100%|██████████| 1338/1338 [04:10<00:00,  5.34it/s]



✅ Proceso completo. Revisa la carpeta:
/content/drive/MyDrive/MNA_ProyectoIntegrador/voting_ensemble_results
📄 CSV resumen creado en:
/content/drive/MyDrive/MNA_ProyectoIntegrador/voting_ensemble_results/predicciones_ensemble.csv


In [10]:
from sklearn.metrics import precision_score, recall_score, f1_score
import os

# Rutas
gt_dir = '/content/drive/MyDrive/MNA_ProyectoIntegrador/galaxy_dataset_2/labels/val'
pred_dir = '/content/drive/MyDrive/MNA_ProyectoIntegrador/voting_ensemble_results'

y_true = []
y_pred = []

# Archivos en el conjunto de validación
gt_files = [f for f in os.listdir(gt_dir) if f.endswith('.txt')]

for fname in gt_files:
    gt_path = os.path.join(gt_dir, fname)
    pred_path = os.path.join(pred_dir, fname)

    # === Ground truth ===
    with open(gt_path, 'r') as f:
        gt_lines = f.readlines()
    has_bar_gt = len(gt_lines) > 0
    y_true.append(1 if has_bar_gt else 0)

    # === Predicción del ensamble ===
    if os.path.exists(pred_path):
        with open(pred_path, 'r') as f:
            pred_lines = f.readlines()
        has_bar_pred = len(pred_lines) > 0
    else:
        has_bar_pred = False

    y_pred.append(1 if has_bar_pred else 0)

# === Métricas
precision = precision_score(y_true, y_pred)
recall = recall_score(y_true, y_pred)
f1 = f1_score(y_true, y_pred)

# === Resultados
print(" Evaluación del ensamble Voting:")
print(f"Precision: {precision:.4f}")
print(f"Recall:    {recall:.4f}")
print(f"F1-score:  {f1:.4f}")


 Evaluación del ensamble Voting:
Precision: 0.6821
Recall:    0.7504
F1-score:  0.7146


### Voting con umbral de confianza de 0.35, IoU de 0.5 y número de votos mínimo de 3 de los 4 modelos

In [11]:
from google.colab import drive
drive.mount('/content/drive')

from ultralytics import YOLO
import os
import cv2
import numpy as np
from tqdm import tqdm
import shutil
import pandas as pd

# === Umbral de confianza mínimo ===
CONFIDENCE_THRESHOLD = 0.35

# === Rutas ===
model_paths = [
    '/content/drive/MyDrive/MNA_ProyectoIntegrador/modelos_yolo/best_v8s_LogDiff.pt',
    '/content/drive/MyDrive/MNA_ProyectoIntegrador/modelos_yolo/best_v8m_LogDiff.pt',
    '/content/drive/MyDrive/MNA_ProyectoIntegrador/modelos_yolo/best_v8l_LogDiff.pt',
    '/content/drive/MyDrive/MNA_ProyectoIntegrador/modelos_yolo/best_v8x_LogDiff.pt'
]

image_dir = '/content/drive/MyDrive/MNA_ProyectoIntegrador/galaxy_dataset_2/images/val'
output_dir = '/content/drive/MyDrive/MNA_ProyectoIntegrador/voting_ensemble_results'
csv_output_path = os.path.join(output_dir, 'predicciones_ensemble.csv')

# === Limpiar carpeta de salida ===
if os.path.exists(output_dir):
    shutil.rmtree(output_dir)
os.makedirs(output_dir)

# === Cargar modelos ===
models = [YOLO(p) for p in model_paths]

# === Funciones auxiliares ===
def iou(box1, box2):
    xA, yA = max(box1[0], box2[0]), max(box1[1], box2[1])
    xB, yB = min(box1[2], box2[2]), min(box1[3], box2[3])
    interArea = max(0, xB - xA) * max(0, yB - yA)
    box1Area = (box1[2] - box1[0]) * (box1[3] - box1[1])
    box2Area = (box2[2] - box2[0]) * (box2[3] - box2[1])
    return interArea / float(box1Area + box2Area - interArea + 1e-6)

def ensemble_predictions(results_list, iou_thr=0.5, vote_threshold=3):
    all_boxes = []
    for model_idx, result in enumerate(results_list):
        for box in result.boxes:
            conf = box.conf[0].cpu().item()
            if conf < CONFIDENCE_THRESHOLD:
                continue  # Filtrar detecciones de baja confianza

            coords = box.xyxy[0].cpu().numpy()
            cls = int(box.cls[0].cpu().item())
            all_boxes.append((coords, conf, cls, model_idx))  # incluir ID del modelo

    grouped = []
    used = set()

    for i in range(len(all_boxes)):
        if i in used:
            continue
        group = [all_boxes[i]]
        model_ids = {all_boxes[i][3]}

        for j in range(i + 1, len(all_boxes)):
            if j in used:
                continue
            if all_boxes[i][2] == all_boxes[j][2] and iou(all_boxes[i][0], all_boxes[j][0]) >= iou_thr:
                if all_boxes[j][3] not in model_ids:
                    group.append(all_boxes[j])
                    model_ids.add(all_boxes[j][3])
                    used.add(j)
        used.add(i)

        if len(model_ids) >= vote_threshold:
            boxes_np = np.array([g[0] for g in group])
            avg_box = boxes_np.mean(axis=0)
            avg_conf = np.mean([g[1] for g in group])
            cls = group[0][2]
            grouped.append((avg_box, avg_conf, cls, len(model_ids)))

    # Validar conflictos
    final_detections = []
    for i, (box_i, conf_i, cls_i, votes_i) in enumerate(grouped):
        conflict = False
        for j, (box_j, conf_j, cls_j, votes_j) in enumerate(grouped):
            if i == j:
                continue
            if iou(box_i, box_j) >= iou_thr and cls_i != cls_j:
                if votes_i > votes_j or (votes_i == votes_j and conf_i > conf_j):
                    continue
                else:
                    conflict = True
                    break
        if not conflict:
            final_detections.append((box_i, conf_i, cls_i, votes_i))

    return final_detections

def convert_to_yolo_format(box, img_width, img_height):
    x1, y1, x2, y2 = box
    x_center = (x1 + x2) / 2.0 / img_width
    y_center = (y1 + y2) / 2.0 / img_height
    width = (x2 - x1) / img_width
    height = (y2 - y1) / img_height
    return x_center, y_center, width, height

# === Procesamiento ===
image_paths = [os.path.join(image_dir, f) for f in os.listdir(image_dir) if f.lower().endswith(('.jpg', '.png'))]
csv_data = []

for img_path in tqdm(image_paths):
    img = cv2.imread(img_path)
    img_height, img_width = img.shape[:2]
    results_list = [model(img)[0] for model in models]
    final_detections = ensemble_predictions(results_list)

    filename = os.path.splitext(os.path.basename(img_path))[0]
    cv2.imwrite(os.path.join(output_dir, f"{filename}.jpg"), img)

    with open(os.path.join(output_dir, f"{filename}.txt"), 'w') as f:
        for box, conf, cls, votes in final_detections:
            x_center, y_center, width, height = convert_to_yolo_format(box, img_width, img_height)
            f.write(f"{cls} {x_center:.6f} {y_center:.6f} {width:.6f} {height:.6f} {conf:.4f}\n")
            csv_data.append({
                "image": f"{filename}.jpg",
                "class": cls,
                "x_center": x_center,
                "y_center": y_center,
                "width": width,
                "height": height,
                "confidence": conf,
                "votes": votes
            })

# Guardar CSV
pd.DataFrame(csv_data).to_csv(csv_output_path, index=False)

print(f"\n Proceso completo. Revisa la carpeta:\n{output_dir}")
print(f" CSV resumen creado en:\n{csv_output_path}")


Drive already mounted at /content/drive; to attempt to forcibly remount, call drive.mount("/content/drive", force_remount=True).


  0%|          | 0/1338 [00:00<?, ?it/s]


0: 640x640 1 barra, 16.2ms
Speed: 2.2ms preprocess, 16.2ms inference, 1.7ms postprocess per image at shape (1, 3, 640, 640)

0: 640x640 1 barra, 36.9ms
Speed: 1.9ms preprocess, 36.9ms inference, 1.5ms postprocess per image at shape (1, 3, 640, 640)

0: 640x640 1 barra, 61.3ms
Speed: 2.0ms preprocess, 61.3ms inference, 1.6ms postprocess per image at shape (1, 3, 640, 640)

0: 640x640 1 barra, 69.1ms
Speed: 2.0ms preprocess, 69.1ms inference, 1.9ms postprocess per image at shape (1, 3, 640, 640)


  0%|          | 1/1338 [00:02<1:01:07,  2.74s/it]


0: 640x640 1 barra, 11.4ms
Speed: 1.9ms preprocess, 11.4ms inference, 1.4ms postprocess per image at shape (1, 3, 640, 640)

0: 640x640 1 barra, 25.0ms
Speed: 1.7ms preprocess, 25.0ms inference, 1.4ms postprocess per image at shape (1, 3, 640, 640)

0: 640x640 1 barra, 42.6ms
Speed: 1.7ms preprocess, 42.6ms inference, 1.5ms postprocess per image at shape (1, 3, 640, 640)

0: 640x640 2 barras, 62.2ms
Speed: 2.3ms preprocess, 62.2ms inference, 1.6ms postprocess per image at shape (1, 3, 640, 640)


...


0: 640x640 (no detections), 9.2ms
Speed: 1.8ms preprocess, 9.2ms inference, 0.7ms postprocess per image at shape (1, 3, 640, 640)

0: 640x640 1 barra, 18.6ms
Speed: 1.9ms preprocess, 18.6ms inference, 1.4ms postprocess per image at shape (1, 3, 640, 640)

0: 640x640 1 barra, 32.5ms
Speed: 1.7ms preprocess, 32.5ms inference, 1.9ms postprocess per image at shape (1, 3, 640, 640)

0: 640x640 2 barras, 60.7ms
Speed: 1.9ms preprocess, 60.7ms inference, 1.6ms postprocess per image at shape (1, 3, 640, 640)


100%|█████████▉| 1337/1338 [04:06<00:00,  5.75it/s]


0: 640x640 2 barras, 8.8ms
Speed: 2.1ms preprocess, 8.8ms inference, 1.5ms postprocess per image at shape (1, 3, 640, 640)

0: 640x640 (no detections), 18.8ms
Speed: 2.0ms preprocess, 18.8ms inference, 0.7ms postprocess per image at shape (1, 3, 640, 640)

0: 640x640 (no detections), 37.1ms
Speed: 1.7ms preprocess, 37.1ms inference, 1.0ms postprocess per image at shape (1, 3, 640, 640)

0: 640x640 (no detections), 63.1ms
Speed: 1.9ms preprocess, 63.1ms inference, 1.2ms postprocess per image at shape (1, 3, 640, 640)


100%|██████████| 1338/1338 [04:06<00:00,  5.43it/s]


✅ Proceso completo. Revisa la carpeta:
/content/drive/MyDrive/MNA_ProyectoIntegrador/voting_ensemble_results
📄 CSV resumen creado en:
/content/drive/MyDrive/MNA_ProyectoIntegrador/voting_ensemble_results/predicciones_ensemble.csv


In [12]:
from sklearn.metrics import precision_score, recall_score, f1_score
import os

# Rutas
gt_dir = '/content/drive/MyDrive/MNA_ProyectoIntegrador/galaxy_dataset_2/labels/val'
pred_dir = '/content/drive/MyDrive/MNA_ProyectoIntegrador/voting_ensemble_results'

y_true = []
y_pred = []

# Archivos en el conjunto de validación
gt_files = [f for f in os.listdir(gt_dir) if f.endswith('.txt')]

for fname in gt_files:
    gt_path = os.path.join(gt_dir, fname)
    pred_path = os.path.join(pred_dir, fname)

    # === Ground truth ===
    with open(gt_path, 'r') as f:
        gt_lines = f.readlines()
    has_bar_gt = len(gt_lines) > 0
    y_true.append(1 if has_bar_gt else 0)

    # === Predicción del ensamble ===
    if os.path.exists(pred_path):
        with open(pred_path, 'r') as f:
            pred_lines = f.readlines()
        has_bar_pred = len(pred_lines) > 0
    else:
        has_bar_pred = False

    y_pred.append(1 if has_bar_pred else 0)

# === Métricas
precision = precision_score(y_true, y_pred)
recall = recall_score(y_true, y_pred)
f1 = f1_score(y_true, y_pred)

# === Resultados
print(" Evaluación del ensamble Voting:")
print(f"Precision: {precision:.4f}")
print(f"Recall:    {recall:.4f}")
print(f"F1-score:  {f1:.4f}")


 Evaluación del ensamble Voting:
Precision: 0.6703
Recall:    0.8356
F1-score:  0.7438


### Voting con umbral de confianza de 0.35, IoU de 0.5 y número de votos mínimo de 2 de los 4 modelos

In [14]:
from google.colab import drive
drive.mount('/content/drive')

from ultralytics import YOLO
import os
import cv2
import numpy as np
from tqdm import tqdm
import shutil
import pandas as pd

# === Umbral de confianza mínimo ===
CONFIDENCE_THRESHOLD = 0.35

# === Rutas ===
model_paths = [
    '/content/drive/MyDrive/MNA_ProyectoIntegrador/modelos_yolo/best_v8s_LogDiff.pt',
    '/content/drive/MyDrive/MNA_ProyectoIntegrador/modelos_yolo/best_v8m_LogDiff.pt',
    '/content/drive/MyDrive/MNA_ProyectoIntegrador/modelos_yolo/best_v8l_LogDiff.pt',
    '/content/drive/MyDrive/MNA_ProyectoIntegrador/modelos_yolo/best_v8x_LogDiff.pt'
]

image_dir = '/content/drive/MyDrive/MNA_ProyectoIntegrador/galaxy_dataset_2/images/val'
output_dir = '/content/drive/MyDrive/MNA_ProyectoIntegrador/voting_ensemble_results'
csv_output_path = os.path.join(output_dir, 'predicciones_ensemble.csv')

# === Limpiar carpeta de salida ===
if os.path.exists(output_dir):
    shutil.rmtree(output_dir)
os.makedirs(output_dir)

# === Cargar modelos ===
models = [YOLO(p) for p in model_paths]

# === Funciones auxiliares ===
def iou(box1, box2):
    xA, yA = max(box1[0], box2[0]), max(box1[1], box2[1])
    xB, yB = min(box1[2], box2[2]), min(box1[3], box2[3])
    interArea = max(0, xB - xA) * max(0, yB - yA)
    box1Area = (box1[2] - box1[0]) * (box1[3] - box1[1])
    box2Area = (box2[2] - box2[0]) * (box2[3] - box2[1])
    return interArea / float(box1Area + box2Area - interArea + 1e-6)

def ensemble_predictions(results_list, iou_thr=0.5, vote_threshold=2):
    all_boxes = []
    for model_idx, result in enumerate(results_list):
        for box in result.boxes:
            conf = box.conf[0].cpu().item()
            if conf < CONFIDENCE_THRESHOLD:
                continue  # Filtrar detecciones de baja confianza

            coords = box.xyxy[0].cpu().numpy()
            cls = int(box.cls[0].cpu().item())
            all_boxes.append((coords, conf, cls, model_idx))  # incluir ID del modelo

    grouped = []
    used = set()

    for i in range(len(all_boxes)):
        if i in used:
            continue
        group = [all_boxes[i]]
        model_ids = {all_boxes[i][3]}

        for j in range(i + 1, len(all_boxes)):
            if j in used:
                continue
            if all_boxes[i][2] == all_boxes[j][2] and iou(all_boxes[i][0], all_boxes[j][0]) >= iou_thr:
                if all_boxes[j][3] not in model_ids:
                    group.append(all_boxes[j])
                    model_ids.add(all_boxes[j][3])
                    used.add(j)
        used.add(i)

        if len(model_ids) >= vote_threshold:
            boxes_np = np.array([g[0] for g in group])
            avg_box = boxes_np.mean(axis=0)
            avg_conf = np.mean([g[1] for g in group])
            cls = group[0][2]
            grouped.append((avg_box, avg_conf, cls, len(model_ids)))

    # Validar conflictos
    final_detections = []
    for i, (box_i, conf_i, cls_i, votes_i) in enumerate(grouped):
        conflict = False
        for j, (box_j, conf_j, cls_j, votes_j) in enumerate(grouped):
            if i == j:
                continue
            if iou(box_i, box_j) >= iou_thr and cls_i != cls_j:
                if votes_i > votes_j or (votes_i == votes_j and conf_i > conf_j):
                    continue
                else:
                    conflict = True
                    break
        if not conflict:
            final_detections.append((box_i, conf_i, cls_i, votes_i))

    return final_detections

def convert_to_yolo_format(box, img_width, img_height):
    x1, y1, x2, y2 = box
    x_center = (x1 + x2) / 2.0 / img_width
    y_center = (y1 + y2) / 2.0 / img_height
    width = (x2 - x1) / img_width
    height = (y2 - y1) / img_height
    return x_center, y_center, width, height

# === Procesamiento ===
image_paths = [os.path.join(image_dir, f) for f in os.listdir(image_dir) if f.lower().endswith(('.jpg', '.png'))]
csv_data = []

for img_path in tqdm(image_paths):
    img = cv2.imread(img_path)
    img_height, img_width = img.shape[:2]
    results_list = [model(img)[0] for model in models]
    final_detections = ensemble_predictions(results_list)

    filename = os.path.splitext(os.path.basename(img_path))[0]
    cv2.imwrite(os.path.join(output_dir, f"{filename}.jpg"), img)

    with open(os.path.join(output_dir, f"{filename}.txt"), 'w') as f:
        for box, conf, cls, votes in final_detections:
            x_center, y_center, width, height = convert_to_yolo_format(box, img_width, img_height)
            f.write(f"{cls} {x_center:.6f} {y_center:.6f} {width:.6f} {height:.6f} {conf:.4f}\n")
            csv_data.append({
                "image": f"{filename}.jpg",
                "class": cls,
                "x_center": x_center,
                "y_center": y_center,
                "width": width,
                "height": height,
                "confidence": conf,
                "votes": votes
            })

# Guardar CSV
pd.DataFrame(csv_data).to_csv(csv_output_path, index=False)

print(f"\nProceso completo. Revisa la carpeta:\n{output_dir}")
print(f"CSV resumen creado en:\n{csv_output_path}")


Drive already mounted at /content/drive; to attempt to forcibly remount, call drive.mount("/content/drive", force_remount=True).


  0%|          | 0/1338 [00:00<?, ?it/s]


0: 640x640 1 barra, 16.2ms
Speed: 3.5ms preprocess, 16.2ms inference, 1.5ms postprocess per image at shape (1, 3, 640, 640)

0: 640x640 1 barra, 37.0ms
Speed: 2.0ms preprocess, 37.0ms inference, 1.6ms postprocess per image at shape (1, 3, 640, 640)

0: 640x640 1 barra, 59.6ms
Speed: 2.0ms preprocess, 59.6ms inference, 1.5ms postprocess per image at shape (1, 3, 640, 640)

0: 640x640 1 barra, 63.6ms
Speed: 2.0ms preprocess, 63.6ms inference, 1.6ms postprocess per image at shape (1, 3, 640, 640)


  0%|          | 1/1338 [00:02<59:33,  2.67s/it]


0: 640x640 1 barra, 8.6ms
Speed: 2.0ms preprocess, 8.6ms inference, 1.4ms postprocess per image at shape (1, 3, 640, 640)

0: 640x640 1 barra, 18.3ms
Speed: 1.8ms preprocess, 18.3ms inference, 1.3ms postprocess per image at shape (1, 3, 640, 640)

0: 640x640 1 barra, 32.6ms
Speed: 1.8ms preprocess, 32.6ms inference, 1.4ms postprocess per image at shape (1, 3, 640, 640)

0: 640x640 2 barras, 61.6ms
Speed: 2.1ms preprocess, 61.6ms inference, 1.5ms postprocess per image at shape (1, 3, 640, 640)


...


0: 640x640 (no detections), 8.6ms
Speed: 1.9ms preprocess, 8.6ms inference, 0.9ms postprocess per image at shape (1, 3, 640, 640)

0: 640x640 1 barra, 18.2ms
Speed: 1.8ms preprocess, 18.2ms inference, 1.4ms postprocess per image at shape (1, 3, 640, 640)

0: 640x640 1 barra, 37.3ms
Speed: 2.0ms preprocess, 37.3ms inference, 1.4ms postprocess per image at shape (1, 3, 640, 640)

0: 640x640 2 barras, 62.7ms
Speed: 1.8ms preprocess, 62.7ms inference, 1.5ms postprocess per image at shape (1, 3, 640, 640)


100%|█████████▉| 1337/1338 [04:00<00:00,  5.51it/s]


0: 640x640 2 barras, 8.9ms
Speed: 2.0ms preprocess, 8.9ms inference, 1.9ms postprocess per image at shape (1, 3, 640, 640)

0: 640x640 (no detections), 18.3ms
Speed: 1.7ms preprocess, 18.3ms inference, 0.7ms postprocess per image at shape (1, 3, 640, 640)

0: 640x640 (no detections), 31.5ms
Speed: 2.1ms preprocess, 31.5ms inference, 0.9ms postprocess per image at shape (1, 3, 640, 640)

0: 640x640 (no detections), 62.7ms
Speed: 1.9ms preprocess, 62.7ms inference, 1.0ms postprocess per image at shape (1, 3, 640, 640)


100%|██████████| 1338/1338 [04:00<00:00,  5.56it/s]



Proceso completo. Revisa la carpeta:
/content/drive/MyDrive/MNA_ProyectoIntegrador/voting_ensemble_results
CSV resumen creado en:
/content/drive/MyDrive/MNA_ProyectoIntegrador/voting_ensemble_results/predicciones_ensemble.csv


In [15]:
from sklearn.metrics import precision_score, recall_score, f1_score
import os

# Rutas
gt_dir = '/content/drive/MyDrive/MNA_ProyectoIntegrador/galaxy_dataset_2/labels/val'
pred_dir = '/content/drive/MyDrive/MNA_ProyectoIntegrador/voting_ensemble_results'

y_true = []
y_pred = []

# Archivos en el conjunto de validación
gt_files = [f for f in os.listdir(gt_dir) if f.endswith('.txt')]

for fname in gt_files:
    gt_path = os.path.join(gt_dir, fname)
    pred_path = os.path.join(pred_dir, fname)

    # === Ground truth ===
    with open(gt_path, 'r') as f:
        gt_lines = f.readlines()
    has_bar_gt = len(gt_lines) > 0
    y_true.append(1 if has_bar_gt else 0)

    # === Predicción del ensamble ===
    if os.path.exists(pred_path):
        with open(pred_path, 'r') as f:
            pred_lines = f.readlines()
        has_bar_pred = len(pred_lines) > 0
    else:
        has_bar_pred = False

    y_pred.append(1 if has_bar_pred else 0)

# === Métricas
precision = precision_score(y_true, y_pred)
recall = recall_score(y_true, y_pred)
f1 = f1_score(y_true, y_pred)

# === Resultados
print(" Evaluación del ensamble Voting:")
print(f"Precision: {precision:.4f}")
print(f"Recall:    {recall:.4f}")
print(f"F1-score:  {f1:.4f}")


 Evaluación del ensamble Voting:
Precision: 0.6070
Recall:    0.9118
F1-score:  0.7288


### Voting con umbral de confianza de 0.25, IoU de 0.5 y número de votos mínimo de 2 de los 4 modelos

In [16]:
from google.colab import drive
drive.mount('/content/drive')

from ultralytics import YOLO
import os
import cv2
import numpy as np
from tqdm import tqdm
import shutil
import pandas as pd

# === Umbral de confianza mínimo ===
CONFIDENCE_THRESHOLD = 0.25

# === Rutas ===
model_paths = [
    '/content/drive/MyDrive/MNA_ProyectoIntegrador/modelos_yolo/best_v8s_LogDiff.pt',
    '/content/drive/MyDrive/MNA_ProyectoIntegrador/modelos_yolo/best_v8m_LogDiff.pt',
    '/content/drive/MyDrive/MNA_ProyectoIntegrador/modelos_yolo/best_v8l_LogDiff.pt',
    '/content/drive/MyDrive/MNA_ProyectoIntegrador/modelos_yolo/best_v8x_LogDiff.pt'
]

image_dir = '/content/drive/MyDrive/MNA_ProyectoIntegrador/galaxy_dataset_2/images/val'
output_dir = '/content/drive/MyDrive/MNA_ProyectoIntegrador/voting_ensemble_results'
csv_output_path = os.path.join(output_dir, 'predicciones_ensemble.csv')

# === Limpiar carpeta de salida ===
if os.path.exists(output_dir):
    shutil.rmtree(output_dir)
os.makedirs(output_dir)

# === Cargar modelos ===
models = [YOLO(p) for p in model_paths]

# === Funciones auxiliares ===
def iou(box1, box2):
    xA, yA = max(box1[0], box2[0]), max(box1[1], box2[1])
    xB, yB = min(box1[2], box2[2]), min(box1[3], box2[3])
    interArea = max(0, xB - xA) * max(0, yB - yA)
    box1Area = (box1[2] - box1[0]) * (box1[3] - box1[1])
    box2Area = (box2[2] - box2[0]) * (box2[3] - box2[1])
    return interArea / float(box1Area + box2Area - interArea + 1e-6)

def ensemble_predictions(results_list, iou_thr=0.5, vote_threshold=2):
    all_boxes = []
    for model_idx, result in enumerate(results_list):
        for box in result.boxes:
            conf = box.conf[0].cpu().item()
            if conf < CONFIDENCE_THRESHOLD:
                continue  # Filtrar detecciones de baja confianza

            coords = box.xyxy[0].cpu().numpy()
            cls = int(box.cls[0].cpu().item())
            all_boxes.append((coords, conf, cls, model_idx))  # incluir ID del modelo

    grouped = []
    used = set()

    for i in range(len(all_boxes)):
        if i in used:
            continue
        group = [all_boxes[i]]
        model_ids = {all_boxes[i][3]}

        for j in range(i + 1, len(all_boxes)):
            if j in used:
                continue
            if all_boxes[i][2] == all_boxes[j][2] and iou(all_boxes[i][0], all_boxes[j][0]) >= iou_thr:
                if all_boxes[j][3] not in model_ids:
                    group.append(all_boxes[j])
                    model_ids.add(all_boxes[j][3])
                    used.add(j)
        used.add(i)

        if len(model_ids) >= vote_threshold:
            boxes_np = np.array([g[0] for g in group])
            avg_box = boxes_np.mean(axis=0)
            avg_conf = np.mean([g[1] for g in group])
            cls = group[0][2]
            grouped.append((avg_box, avg_conf, cls, len(model_ids)))

    # Validar conflictos
    final_detections = []
    for i, (box_i, conf_i, cls_i, votes_i) in enumerate(grouped):
        conflict = False
        for j, (box_j, conf_j, cls_j, votes_j) in enumerate(grouped):
            if i == j:
                continue
            if iou(box_i, box_j) >= iou_thr and cls_i != cls_j:
                if votes_i > votes_j or (votes_i == votes_j and conf_i > conf_j):
                    continue
                else:
                    conflict = True
                    break
        if not conflict:
            final_detections.append((box_i, conf_i, cls_i, votes_i))

    return final_detections

def convert_to_yolo_format(box, img_width, img_height):
    x1, y1, x2, y2 = box
    x_center = (x1 + x2) / 2.0 / img_width
    y_center = (y1 + y2) / 2.0 / img_height
    width = (x2 - x1) / img_width
    height = (y2 - y1) / img_height
    return x_center, y_center, width, height

# === Procesamiento ===
image_paths = [os.path.join(image_dir, f) for f in os.listdir(image_dir) if f.lower().endswith(('.jpg', '.png'))]
csv_data = []

for img_path in tqdm(image_paths):
    img = cv2.imread(img_path)
    img_height, img_width = img.shape[:2]
    results_list = [model(img)[0] for model in models]
    final_detections = ensemble_predictions(results_list)

    filename = os.path.splitext(os.path.basename(img_path))[0]
    cv2.imwrite(os.path.join(output_dir, f"{filename}.jpg"), img)

    with open(os.path.join(output_dir, f"{filename}.txt"), 'w') as f:
        for box, conf, cls, votes in final_detections:
            x_center, y_center, width, height = convert_to_yolo_format(box, img_width, img_height)
            f.write(f"{cls} {x_center:.6f} {y_center:.6f} {width:.6f} {height:.6f} {conf:.4f}\n")
            csv_data.append({
                "image": f"{filename}.jpg",
                "class": cls,
                "x_center": x_center,
                "y_center": y_center,
                "width": width,
                "height": height,
                "confidence": conf,
                "votes": votes
            })

# Guardar CSV
pd.DataFrame(csv_data).to_csv(csv_output_path, index=False)

print(f"\nProceso completo. Revisa la carpeta:\n{output_dir}")
print(f"CSV resumen creado en:\n{csv_output_path}")


Drive already mounted at /content/drive; to attempt to forcibly remount, call drive.mount("/content/drive", force_remount=True).


  0%|          | 0/1338 [00:00<?, ?it/s]


0: 640x640 1 barra, 16.2ms
Speed: 2.1ms preprocess, 16.2ms inference, 1.6ms postprocess per image at shape (1, 3, 640, 640)

0: 640x640 1 barra, 36.9ms
Speed: 2.0ms preprocess, 36.9ms inference, 2.0ms postprocess per image at shape (1, 3, 640, 640)

0: 640x640 1 barra, 62.5ms
Speed: 1.9ms preprocess, 62.5ms inference, 1.5ms postprocess per image at shape (1, 3, 640, 640)

0: 640x640 1 barra, 80.6ms
Speed: 2.0ms preprocess, 80.6ms inference, 1.5ms postprocess per image at shape (1, 3, 640, 640)


  0%|          | 1/1338 [00:02<1:01:51,  2.78s/it]


0: 640x640 1 barra, 13.7ms
Speed: 1.9ms preprocess, 13.7ms inference, 1.4ms postprocess per image at shape (1, 3, 640, 640)

0: 640x640 1 barra, 30.9ms
Speed: 2.0ms preprocess, 30.9ms inference, 1.5ms postprocess per image at shape (1, 3, 640, 640)

0: 640x640 1 barra, 38.2ms
Speed: 2.0ms preprocess, 38.2ms inference, 1.4ms postprocess per image at shape (1, 3, 640, 640)

0: 640x640 2 barras, 61.6ms
Speed: 1.7ms preprocess, 61.6ms inference, 1.4ms postprocess per image at shape (1, 3, 640, 640)


...


0: 640x640 (no detections), 8.9ms
Speed: 2.0ms preprocess, 8.9ms inference, 0.8ms postprocess per image at shape (1, 3, 640, 640)

0: 640x640 1 barra, 18.5ms
Speed: 1.9ms preprocess, 18.5ms inference, 1.8ms postprocess per image at shape (1, 3, 640, 640)

0: 640x640 1 barra, 33.3ms
Speed: 2.0ms preprocess, 33.3ms inference, 2.1ms postprocess per image at shape (1, 3, 640, 640)

0: 640x640 2 barras, 60.7ms
Speed: 2.5ms preprocess, 60.7ms inference, 2.6ms postprocess per image at shape (1, 3, 640, 640)


100%|█████████▉| 1337/1338 [04:07<00:00,  5.45it/s]


0: 640x640 2 barras, 8.2ms
Speed: 2.3ms preprocess, 8.2ms inference, 1.5ms postprocess per image at shape (1, 3, 640, 640)

0: 640x640 (no detections), 17.8ms
Speed: 2.0ms preprocess, 17.8ms inference, 0.8ms postprocess per image at shape (1, 3, 640, 640)

0: 640x640 (no detections), 34.9ms
Speed: 1.9ms preprocess, 34.9ms inference, 1.0ms postprocess per image at shape (1, 3, 640, 640)

0: 640x640 (no detections), 63.4ms
Speed: 2.0ms preprocess, 63.4ms inference, 1.0ms postprocess per image at shape (1, 3, 640, 640)


100%|██████████| 1338/1338 [04:08<00:00,  5.39it/s]


Proceso completo. Revisa la carpeta:
/content/drive/MyDrive/MNA_ProyectoIntegrador/voting_ensemble_results
CSV resumen creado en:
/content/drive/MyDrive/MNA_ProyectoIntegrador/voting_ensemble_results/predicciones_ensemble.csv


In [17]:
from sklearn.metrics import precision_score, recall_score, f1_score
import os

# Rutas
gt_dir = '/content/drive/MyDrive/MNA_ProyectoIntegrador/galaxy_dataset_2/labels/val'
pred_dir = '/content/drive/MyDrive/MNA_ProyectoIntegrador/voting_ensemble_results'

y_true = []
y_pred = []

# Archivos en el conjunto de validación
gt_files = [f for f in os.listdir(gt_dir) if f.endswith('.txt')]

for fname in gt_files:
    gt_path = os.path.join(gt_dir, fname)
    pred_path = os.path.join(pred_dir, fname)

    # === Ground truth ===
    with open(gt_path, 'r') as f:
        gt_lines = f.readlines()
    has_bar_gt = len(gt_lines) > 0
    y_true.append(1 if has_bar_gt else 0)

    # === Predicción del ensamble ===
    if os.path.exists(pred_path):
        with open(pred_path, 'r') as f:
            pred_lines = f.readlines()
        has_bar_pred = len(pred_lines) > 0
    else:
        has_bar_pred = False

    y_pred.append(1 if has_bar_pred else 0)

# === Métricas
precision = precision_score(y_true, y_pred)
recall = recall_score(y_true, y_pred)
f1 = f1_score(y_true, y_pred)

# === Resultados
print(" Evaluación del ensamble Voting:")
print(f"Precision: {precision:.4f}")
print(f"Recall:    {recall:.4f}")
print(f"F1-score:  {f1:.4f}")


 Evaluación del ensamble Voting:
Precision: 0.5628
Recall:    0.9641
F1-score:  0.7107


### Voting con umbral de confianza de 0.35, IoU de 0.45 y número de votos mínimo de 3 de los 4 modelos

In [18]:
from google.colab import drive
drive.mount('/content/drive')

from ultralytics import YOLO
import os
import cv2
import numpy as np
from tqdm import tqdm
import shutil
import pandas as pd

# === Umbral de confianza mínimo ===
CONFIDENCE_THRESHOLD = 0.35

# === Rutas ===
model_paths = [
    '/content/drive/MyDrive/MNA_ProyectoIntegrador/modelos_yolo/best_v8s_LogDiff.pt',
    '/content/drive/MyDrive/MNA_ProyectoIntegrador/modelos_yolo/best_v8m_LogDiff.pt',
    '/content/drive/MyDrive/MNA_ProyectoIntegrador/modelos_yolo/best_v8l_LogDiff.pt',
    '/content/drive/MyDrive/MNA_ProyectoIntegrador/modelos_yolo/best_v8x_LogDiff.pt'
]

image_dir = '/content/drive/MyDrive/MNA_ProyectoIntegrador/galaxy_dataset_2/images/val'
output_dir = '/content/drive/MyDrive/MNA_ProyectoIntegrador/voting_ensemble_results'
csv_output_path = os.path.join(output_dir, 'predicciones_ensemble.csv')

# === Limpiar carpeta de salida ===
if os.path.exists(output_dir):
    shutil.rmtree(output_dir)
os.makedirs(output_dir)

# === Cargar modelos ===
models = [YOLO(p) for p in model_paths]

# === Funciones auxiliares ===
def iou(box1, box2):
    xA, yA = max(box1[0], box2[0]), max(box1[1], box2[1])
    xB, yB = min(box1[2], box2[2]), min(box1[3], box2[3])
    interArea = max(0, xB - xA) * max(0, yB - yA)
    box1Area = (box1[2] - box1[0]) * (box1[3] - box1[1])
    box2Area = (box2[2] - box2[0]) * (box2[3] - box2[1])
    return interArea / float(box1Area + box2Area - interArea + 1e-6)

def ensemble_predictions(results_list, iou_thr=0.45, vote_threshold=3):
    all_boxes = []
    for model_idx, result in enumerate(results_list):
        for box in result.boxes:
            conf = box.conf[0].cpu().item()
            if conf < CONFIDENCE_THRESHOLD:
                continue  # Filtrar detecciones de baja confianza

            coords = box.xyxy[0].cpu().numpy()
            cls = int(box.cls[0].cpu().item())
            all_boxes.append((coords, conf, cls, model_idx))  # incluir ID del modelo

    grouped = []
    used = set()

    for i in range(len(all_boxes)):
        if i in used:
            continue
        group = [all_boxes[i]]
        model_ids = {all_boxes[i][3]}

        for j in range(i + 1, len(all_boxes)):
            if j in used:
                continue
            if all_boxes[i][2] == all_boxes[j][2] and iou(all_boxes[i][0], all_boxes[j][0]) >= iou_thr:
                if all_boxes[j][3] not in model_ids:
                    group.append(all_boxes[j])
                    model_ids.add(all_boxes[j][3])
                    used.add(j)
        used.add(i)

        if len(model_ids) >= vote_threshold:
            boxes_np = np.array([g[0] for g in group])
            avg_box = boxes_np.mean(axis=0)
            avg_conf = np.mean([g[1] for g in group])
            cls = group[0][2]
            grouped.append((avg_box, avg_conf, cls, len(model_ids)))

    # Validar conflictos
    final_detections = []
    for i, (box_i, conf_i, cls_i, votes_i) in enumerate(grouped):
        conflict = False
        for j, (box_j, conf_j, cls_j, votes_j) in enumerate(grouped):
            if i == j:
                continue
            if iou(box_i, box_j) >= iou_thr and cls_i != cls_j:
                if votes_i > votes_j or (votes_i == votes_j and conf_i > conf_j):
                    continue
                else:
                    conflict = True
                    break
        if not conflict:
            final_detections.append((box_i, conf_i, cls_i, votes_i))

    return final_detections

def convert_to_yolo_format(box, img_width, img_height):
    x1, y1, x2, y2 = box
    x_center = (x1 + x2) / 2.0 / img_width
    y_center = (y1 + y2) / 2.0 / img_height
    width = (x2 - x1) / img_width
    height = (y2 - y1) / img_height
    return x_center, y_center, width, height

# === Procesamiento ===
image_paths = [os.path.join(image_dir, f) for f in os.listdir(image_dir) if f.lower().endswith(('.jpg', '.png'))]
csv_data = []

for img_path in tqdm(image_paths):
    img = cv2.imread(img_path)
    img_height, img_width = img.shape[:2]
    results_list = [model(img)[0] for model in models]
    final_detections = ensemble_predictions(results_list)

    filename = os.path.splitext(os.path.basename(img_path))[0]
    cv2.imwrite(os.path.join(output_dir, f"{filename}.jpg"), img)

    with open(os.path.join(output_dir, f"{filename}.txt"), 'w') as f:
        for box, conf, cls, votes in final_detections:
            x_center, y_center, width, height = convert_to_yolo_format(box, img_width, img_height)
            f.write(f"{cls} {x_center:.6f} {y_center:.6f} {width:.6f} {height:.6f} {conf:.4f}\n")
            csv_data.append({
                "image": f"{filename}.jpg",
                "class": cls,
                "x_center": x_center,
                "y_center": y_center,
                "width": width,
                "height": height,
                "confidence": conf,
                "votes": votes
            })

# Guardar CSV
pd.DataFrame(csv_data).to_csv(csv_output_path, index=False)

print(f"\nProceso completo. Revisa la carpeta:\n{output_dir}")
print(f"CSV resumen creado en:\n{csv_output_path}")


Drive already mounted at /content/drive; to attempt to forcibly remount, call drive.mount("/content/drive", force_remount=True).


  0%|          | 0/1338 [00:00<?, ?it/s]


0: 640x640 1 barra, 16.2ms
Speed: 2.1ms preprocess, 16.2ms inference, 1.7ms postprocess per image at shape (1, 3, 640, 640)

0: 640x640 1 barra, 37.0ms
Speed: 2.1ms preprocess, 37.0ms inference, 1.6ms postprocess per image at shape (1, 3, 640, 640)

0: 640x640 1 barra, 59.9ms
Speed: 2.0ms preprocess, 59.9ms inference, 1.6ms postprocess per image at shape (1, 3, 640, 640)

0: 640x640 1 barra, 62.8ms
Speed: 1.9ms preprocess, 62.8ms inference, 1.5ms postprocess per image at shape (1, 3, 640, 640)


  0%|          | 1/1338 [00:02<59:35,  2.67s/it]


0: 640x640 1 barra, 10.8ms
Speed: 1.9ms preprocess, 10.8ms inference, 1.5ms postprocess per image at shape (1, 3, 640, 640)

0: 640x640 1 barra, 24.1ms
Speed: 1.7ms preprocess, 24.1ms inference, 1.3ms postprocess per image at shape (1, 3, 640, 640)

0: 640x640 1 barra, 38.7ms
Speed: 1.6ms preprocess, 38.7ms inference, 1.3ms postprocess per image at shape (1, 3, 640, 640)

0: 640x640 2 barras, 61.2ms
Speed: 1.8ms preprocess, 61.2ms inference, 1.3ms postprocess per image at shape (1, 3, 640, 640)


...


0: 640x640 (no detections), 9.4ms
Speed: 1.9ms preprocess, 9.4ms inference, 0.9ms postprocess per image at shape (1, 3, 640, 640)

0: 640x640 1 barra, 19.0ms
Speed: 2.0ms preprocess, 19.0ms inference, 1.4ms postprocess per image at shape (1, 3, 640, 640)

0: 640x640 1 barra, 33.4ms
Speed: 2.4ms preprocess, 33.4ms inference, 2.4ms postprocess per image at shape (1, 3, 640, 640)

0: 640x640 2 barras, 62.4ms
Speed: 2.1ms preprocess, 62.4ms inference, 1.9ms postprocess per image at shape (1, 3, 640, 640)


100%|█████████▉| 1337/1338 [04:08<00:00,  5.74it/s]


0: 640x640 2 barras, 8.8ms
Speed: 2.2ms preprocess, 8.8ms inference, 1.6ms postprocess per image at shape (1, 3, 640, 640)

0: 640x640 (no detections), 18.2ms
Speed: 1.9ms preprocess, 18.2ms inference, 0.7ms postprocess per image at shape (1, 3, 640, 640)

0: 640x640 (no detections), 35.5ms
Speed: 2.4ms preprocess, 35.5ms inference, 0.9ms postprocess per image at shape (1, 3, 640, 640)

0: 640x640 (no detections), 62.8ms
Speed: 2.8ms preprocess, 62.8ms inference, 0.8ms postprocess per image at shape (1, 3, 640, 640)


100%|██████████| 1338/1338 [04:08<00:00,  5.38it/s]


Proceso completo. Revisa la carpeta:
/content/drive/MyDrive/MNA_ProyectoIntegrador/voting_ensemble_results
CSV resumen creado en:
/content/drive/MyDrive/MNA_ProyectoIntegrador/voting_ensemble_results/predicciones_ensemble.csv


In [19]:
from sklearn.metrics import precision_score, recall_score, f1_score
import os

# Rutas
gt_dir = '/content/drive/MyDrive/MNA_ProyectoIntegrador/galaxy_dataset_2/labels/val'
pred_dir = '/content/drive/MyDrive/MNA_ProyectoIntegrador/voting_ensemble_results'

y_true = []
y_pred = []

# Archivos en el conjunto de validación
gt_files = [f for f in os.listdir(gt_dir) if f.endswith('.txt')]

for fname in gt_files:
    gt_path = os.path.join(gt_dir, fname)
    pred_path = os.path.join(pred_dir, fname)

    # === Ground truth ===
    with open(gt_path, 'r') as f:
        gt_lines = f.readlines()
    has_bar_gt = len(gt_lines) > 0
    y_true.append(1 if has_bar_gt else 0)

    # === Predicción del ensamble ===
    if os.path.exists(pred_path):
        with open(pred_path, 'r') as f:
            pred_lines = f.readlines()
        has_bar_pred = len(pred_lines) > 0
    else:
        has_bar_pred = False

    y_pred.append(1 if has_bar_pred else 0)

# === Métricas
precision = precision_score(y_true, y_pred)
recall = recall_score(y_true, y_pred)
f1 = f1_score(y_true, y_pred)

# === Resultados
print(" Evaluación del ensamble Voting:")
print(f"Precision: {precision:.4f}")
print(f"Recall:    {recall:.4f}")
print(f"F1-score:  {f1:.4f}")


 Evaluación del ensamble Voting:
Precision: 0.6695
Recall:    0.8356
F1-score:  0.7434
